In [ ]:
%conda install jupyter_bokeh


In [3]:
import geopandas as gpd
import pandas as pd
import panel as pn
import numpy as np
import fiona
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objects as go
import json
import pydeck as pdk
from bokeh.models.formatters import PrintfTickFormatter
import folium
from folium.plugins import MarkerCluster
from folium.plugins import Search
import branca



In [5]:
# Initialize extensions
pn.extension()
pn.extension("plotly")
pn.extension("echarts")
pn.extension(design=pn.theme.Material)
pn.extension('tabulator', 'ace', css_files=['https://unpkg.com/leaflet@1.7.1/dist/leaflet.css'])

In [3]:
path_gpkg= "../GEOPKG/Thematic_Data.gpkg"
gdf = gpd.read_file(path_gpkg, layer='well_Capacity_cost')
gdf.head()

fid              Name      XCOORD      YCOORD  Num_Wells    Q_Median_d  \
0  1.0      Archemerberg  225301.250  499157.130       17.0  -7852.580000   
1  2.0     Espelosebroek  220340.095  478421.640       28.0 -11760.192208   
2  3.0  Goor/Herikerberg  235706.700  472184.570       30.0  -3752.000000   
3  4.0       Hammerflier  233271.960  499976.615        5.0  -4330.000000   
4  5.0           Hasselo  250986.830  478539.680        9.0  -1465.720000   

        Q_AVG_d  TOP_fltr_max  BOTTOM_fltr_min       Location  ...  \
0  -8182.148525          1.31           -53.18   Archemerberg  ...   
1 -12032.234310        -20.58           -62.73  Espelosebroek  ...   
2  -3670.600318         -1.06           -57.60           Goor  ...   
3  -4177.560692         -9.85           -52.50    Hammerflier  ...   
4  -1394.213848         -1.42            -9.50        Hasselo  ...   

  Energy_EUR_m3 Chemicals_EUR_m3 Tax_EUR_m3    OPEX LocationSize  \
0        0.0320           0.0152     0.0174  0.0136        Klein   
1        0.0232           0.0496     0.0176  0.0293  Middelgroot   
2        0.0230           0.0532     0.0114  0.0243  Middelgroot   
3        0.1017           0.0292     0.0253  0.1133        Klein   
4        0.1180           0.0075     0.0330  0.1421        Klein   

                  Purification  CO2Cost_EUR_m3 DroughtDamage_EUR_m3  \
0  Geen extra filtratiestappen          0.0113               0.0575   
1  Geen extra filtratiestappen          0.0287               0.0000   
2  Geen extra filtratiestappen          0.0308               0.0460   
3                  Actief kool          0.1341               0.0332   
4  Geen extra filtratiestappen          0.0805               0.0164   

  WaterProduction                       geometry  
0         2795052  POINT (225301.252 499157.129)  
1         4165610  POINT (220340.096 478421.638)  
2         5023530  POINT (233749.993 472759.694)  
3         1426160  POINT (233271.962 499976.613)  
4          350283  POINT (250986.829 478539.680)  

[5 rows x 42 columns]

In [72]:
gdf = gdf.to_crs(epsg=4326)
# Ensure the GeoDataFrame contains only geometries of type Point (pydeck requires point coordinates for plotting)
gdf = gdf[gdf.geometry.type == "Point"]
# Convert the GeoDataFrame to GeoJSON format
# Extract coordinates from the GeoDataFrame
gdf['lon'] = gdf.geometry.x
gdf['lat'] = gdf.geometry.y

gdf.head()

fid              Name      XCOORD      YCOORD  Num_Wells    Q_Median_d  \
0  1.0      Archemerberg  225301.250  499157.130       17.0  -7852.580000   
1  2.0     Espelosebroek  220340.095  478421.640       28.0 -11760.192208   
2  3.0  Goor/Herikerberg  235706.700  472184.570       30.0  -3752.000000   
3  4.0       Hammerflier  233271.960  499976.615        5.0  -4330.000000   
4  5.0           Hasselo  250986.830  478539.680        9.0  -1465.720000   

        Q_AVG_d  TOP_fltr_max  BOTTOM_fltr_min       Location  ... Tax_EUR_m3  \
0  -8182.148525          1.31           -53.18   Archemerberg  ...     0.0174   
1 -12032.234310        -20.58           -62.73  Espelosebroek  ...     0.0176   
2  -3670.600318         -1.06           -57.60           Goor  ...     0.0114   
3  -4177.560692         -9.85           -52.50    Hammerflier  ...     0.0253   
4  -1394.213848         -1.42            -9.50        Hasselo  ...     0.0330   

     OPEX LocationSize                 Purification CO2Cost_EUR_m3  \
0  0.0136        Klein  Geen extra filtratiestappen         0.0113   
1  0.0293  Middelgroot  Geen extra filtratiestappen         0.0287   
2  0.0243  Middelgroot  Geen extra filtratiestappen         0.0308   
3  0.1133        Klein                  Actief kool         0.1341   
4  0.1421        Klein  Geen extra filtratiestappen         0.0805   

   DroughtDamage_EUR_m3  WaterProduction                  geometry       lon  \
0                0.0575          2795052  POINT (6.42195 52.47562)  6.421950   
1                0.0000          4165610  POINT (6.34490 52.28990)  6.344903   
2                0.0460          5023530  POINT (6.54010 52.23726)  6.540100   
3                0.0332          1426160  POINT (6.53944 52.48191)  6.539439   
4                0.0164           350283  POINT (6.79402 52.28647)  6.794022   

         lat  
0  52.475623  
1  52.289898  
2  52.237263  
3  52.481905  
4  52.286467  

[5 rows x 44 columns]

In [28]:
# Load the GeoPackage file
gpkg_file = "../GEOPKG/Thematic_data.gpkg"
layers = fiona.listlayers(gpkg_file)  # Load all layers

# Get Wells Attributes
wells = gpd.read_file(gpkg_file, layer="Well_Capacity_Cost")
# Convert the capacity columns to numeric, setting errors='coerce' will replace non-numeric values with NaN
wells["Permit__Mm3_per_jr_"] = pd.to_numeric(
    wells["Permit__Mm3_per_jr_"], errors="coerce"
)
wells["Extraction_2023__Mm3_per_jr_"] = pd.to_numeric(
    wells["Extraction_2023__Mm3_per_jr_"], errors="coerce"
)
# calculate total costs per m3
wells["totOpex_m3"] = (
    wells["OPEX"]
    + wells["Labor_EUR_m3"]
    + wells["Energy_EUR_m3"]
    + wells["Chemicals_EUR_m3"]
    + wells["Tax_EUR_m3"]
)
wells["env_cost_m3"] = wells["CO2Cost_EUR_m3"] + wells["DroughtDamage_EUR_m3"]


# Initialize a DataFrame to hold the active state and slider values
active_wells_df = gpd.GeoDataFrame(
    {
        "Name": wells["Name"],
        "Num_Wells": wells["Num_Wells"],
        "Balance area": wells["Balansgebied"],
        "Active": [True] * len(wells),
        "Value": wells["Extraction_2023__Mm3_per_jr_"],
        "OPEX_m3": wells["totOpex_m3"],
        "Env_m3": wells["env_cost_m3"],
        "envCost": wells["env_cost_m3"]
        * wells["Extraction_2023__Mm3_per_jr_"]
        * 1000000,
        "OPEX": wells["totOpex_m3"] * wells["Extraction_2023__Mm3_per_jr_"] * 1000000,
        "geometry": wells["geometry"]
    }
)


yearCal = 2022
growRate = 0.0062
demand_capita = 0.130

# Get Destination Attributes
hexagons = gpd.read_file(gpkg_file, layer="H3_Lvl8")


hexagons_filterd = gpd.GeoDataFrame(
    {
        "GRID_ID": hexagons["GRID_ID"],
        "Balance Area": hexagons["Name"],
        "Pop2022": hexagons["Pop_2022"],
        "Current Pop": hexagons["Pop_2022"],
        "Industrial Demand": hexagons["Ind_Demand"],
        "Water Demand": hexagons["Pop_2022"] * 0.130 * 365 / 1000000,

        "geometry" : hexagons["geometry"]
        
    }
)

active_wells_df

Name  Num_Wells  Balance area  Active  Value  OPEX_m3  Env_m3  \
0       Archemerberg       17.0     Reggeland    True   2.89   0.1117  0.0688   
1      Espelosebroek       28.0  Hof v Twente    True   3.69   0.1461  0.0287   
2   Goor/Herikerberg       30.0  Hof v Twente    True   4.95   0.1629  0.0768   
3        Hammerflier        5.0     Reggeland    True   1.57   0.4607  0.1673   
4            Hasselo        9.0    Stedenband    True   0.52   0.6682  0.0969   
5         Hoge Hexel       11.0     Reggeland    True   2.47   0.1510  0.0242   
6             Holten       21.0  Hof v Twente    True   2.48   0.2479  0.0747   
7   Manderveen-Heide       13.0    Dinkelland    True   2.94   0.2398  0.2194   
8          Nijverdal       29.0     Reggeland    True   5.98   0.0996  0.0196   
9          Rodenmors        9.0    Dinkelland    True   1.40   0.5554  0.1797   
10            Losser        3.0    Stedenband    True   1.46   0.3219  0.4320   
11          Weerselo        4.0    Dinkelland    True   0.94   0.1467  0.1816   
12           Wierden       46.0     Reggeland    True   7.80   0.1987  0.2088   

      envCost       OPEX                       geometry  
0    198832.0   322813.0  POINT (225301.252 499157.129)  
1    105903.0   539109.0  POINT (220340.096 478421.638)  
2    380160.0   806355.0  POINT (233749.993 472759.694)  
3    262661.0   723299.0  POINT (233271.962 499976.613)  
4     50388.0   347464.0  POINT (250986.829 478539.680)  
5     59774.0   372970.0  POINT (234838.245 489643.812)  
6    185256.0   614792.0  POINT (227793.763 478797.011)  
7    645036.0   705012.0  POINT (250816.768 496768.824)  
8    117208.0   595608.0  POINT (226615.807 486326.472)  
9    251580.0   777560.0  POINT (267375.991 490176.101)  
10   630720.0   469974.0  POINT (263294.222 476310.267)  
11   170704.0   137898.0  POINT (256253.059 483873.132)  
12  1628640.0  1549860.0  POINT (235353.211 485441.993)

In [9]:
# create map and add attrobutes ### TODO: Check how to join with well active DF
m = folium.Map(location=[52.38, 6.7], zoom_start=10)  # Adjust the center and zoom level as necessary
popup_well = folium.GeoJsonPopup(fields=["Name", "Balance area", "Value"],
                                 aliases=["Well Name", "Balance Area", "Extraction in Mm\u00b3/Year"])
popup_hex = folium.GeoJsonPopup(fields=["Balance Area", "Water Demand", "Current Pop"])
icon_path = "./Assets/Water Icon.png"
icon = folium.CustomIcon(
    icon_path,
    icon_size=(30, 30),
)


colormap = branca.colormap.LinearColormap(
    ["#caf0f8", "#90e0ef", "#00b4d8", "#0077b6", "#03045e"],
    vmin=hexagons_filterd["Water Demand"].quantile(0.0),
    vmax = hexagons_filterd["Water Demand"].quantile(1),
    caption="Total water demand in Mm\u00b3/Year",
)

m


In [22]:
m = folium.Map(location=[52.38, 6.7], zoom_start=10)  # Re-initialize the map to clear layers
        
w = folium.GeoJson(active_wells_df,
                name="Wells", 
                zoom_on_click=True,
                popup=popup_well,
                tooltip=folium.GeoJsonTooltip(fields=["Name"], aliases=["Well Name:"]),
                marker = folium.Marker(icon=folium.Icon(
                                        icon_color='#F9F6EE',
                                        icon='arrow-up-from-ground-water',
                                        prefix='fa'))
                )

h =folium.GeoJson(hexagons_filterd,
                name="Hexagons",
                    style_function=lambda x: {
                        "fillColor": colormap(x["properties"]["Water Demand"])
                        if x["properties"]["Water Demand"] is not None
                        else "#6b6d69",
                        "color": "darkgray",
                        "fillOpacity": 0.8,
                        "weight":  0.7,
                        },
                    popup=popup_hex,
                #    tooltip=folium.GeoJsonTooltip(fields=["Balance Area"], aliases=["Balance Area:"]),
                #    style_function=hexagons_filterd["style"]
                ).add_to(m)

h.add_child(colormap)
folium.LayerControl().add_to(m)


m

In [23]:
def update_layers():
    # Clear existing layers
    m = folium.Map(location=[52.38, 6.7], zoom_start=10)  # Re-initialize the map to clear layers
        
    w = folium.GeoJson(active_wells_df,
                name="Wells", 
                zoom_on_click=True,
                popup=popup_well,
                tooltip=folium.GeoJsonTooltip(fields=["Name"], aliases=["Well Name:"]),
                marker = folium.Marker(icon=folium.Icon(
                                        icon_color='#F9F6EE',
                                        icon='arrow-up-from-ground-water',
                                        prefix='fa'))
                ).add_to(m)

    h =folium.GeoJson(hexagons_filterd,
                name="Hexagons",
                    style_function=lambda x: {
                        "fillColor": colormap(x["properties"]["Water Demand"])
                        if x["properties"]["Water Demand"] is not None
                        else "#6b6d69",
                        "color": "darkgray",
                        "fillOpacity": 0.8,
                        "weight":  0.7,
                        },
                    popup=popup_hex,
                #    tooltip=folium.GeoJsonTooltip(fields=["Balance Area"], aliases=["Balance Area:"]),
                #    style_function=hexagons_filterd["style"]
                ).add_to(m)

    h.add_child(colormap)
    folium.LayerControl().add_to(m)


    return m


In [25]:
update_layers()